# ETL + EDA 

## Importando las Bibliotecas Necesarias

En esta sección, importamos las bibliotecas necesarias para nuestro análisis. 
- pandas para manipulación de datos,
- ydata_profiling y dtale para análisis exploratorio de datos,
- y numpy para operaciones numéricas.

In [1]:
import pandas as pd
import ydata_profiling as ydata
import dtale
import numpy as np

c:\Users\Compumar\Documents\Henry\PI_DA\PI_DA\.venv\Lib\site-packages\numba\core\decorators.py:262: NumbaDeprecationWarning: numba.generated_jit is deprecated. Please see the documentation at: https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-generated-jit for more information and advice on a suitable replacement.
  warnings.warn(msg, NumbaDeprecationWarning)
c:\Users\Compumar\Documents\Henry\PI_DA\PI_DA\.venv\Lib\site-packages\visions\backends\shared\nan_handling.py:50: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @nb.jit


## Cargando el Dataset
A continuación, cargamos nuestro dataset de accidentes de aviones desde un archivo CSV usando pandas.

In [2]:
df_accidentes = pd.read_csv("./data/raw/AccidentesAviones.csv")

## Información General del Dataset
Obtenemos una vista general de la información del dataset, como el número de entradas, el número de columnas y el tipo de datos de cada columna.


In [3]:
df_accidentes.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5008 entries, 0 to 5007
Data columns (total 18 columns):
 #   Column                  Non-Null Count  Dtype 
---  ------                  --------------  ----- 
 0   Unnamed: 0              5008 non-null   int64 
 1   fecha                   5008 non-null   object
 2   HORA declarada          5008 non-null   object
 3   Ruta                    5008 non-null   object
 4   OperadOR                5008 non-null   object
 5   flight_no               5008 non-null   object
 6   route                   5007 non-null   object
 7   ac_type                 5008 non-null   object
 8   registration            5008 non-null   object
 9   cn_ln                   5008 non-null   object
 10  all_aboard              5008 non-null   object
 11  PASAJEROS A BORDO       5008 non-null   object
 12  crew_aboard             5008 non-null   object
 13  cantidad de fallecidos  5008 non-null   object
 14  passenger_fatalities    5008 non-null   object
 15  crew

## Eliminando Columna Innecesaria
Eliminamos la columna 'Unnamed: 0' ya que parece ser un índice duplicado y no aporta información relevante para nuestro análisis.

In [4]:
df_accidentes.drop(columns=['Unnamed: 0'], inplace=True)

Reemplazar '?' con NaN en todo el DataFrame


In [5]:
df_accidentes.replace('?', np.nan, inplace=True)

Verificamos los tipos de datos de cada columna para asegurarnos de que sean apropiados para el análisis. Por ejemplo, las columnas que representan fechas deberían tener un tipo de datos datetime, y las columnas numéricas deberían ser de tipo int o float.


In [6]:
# Mostrar los tipos de datos actuales
print(df_accidentes.dtypes)

fecha                     object
HORA declarada            object
Ruta                      object
OperadOR                  object
flight_no                 object
route                     object
ac_type                   object
registration              object
cn_ln                     object
all_aboard                object
PASAJEROS A BORDO         object
crew_aboard               object
cantidad de fallecidos    object
passenger_fatalities      object
crew_fatalities           object
ground                    object
summary                   object
dtype: object


## Conversión de la columna 'fecha' a datetime

Convertimos la columna 'fecha' a un objeto datetime para facilitar la manipulación y análisis de las fechas en el dataset.


In [7]:
# Conversión de 'fecha'
df_accidentes['fecha'] = pd.to_datetime(df_accidentes['fecha'], errors='coerce')


## Conversión de la columna 'HORA declarada' a time


Definimos una función llamada `convert_to_time` que intenta convertir una entrada a un objeto de tiempo. Si la conversión falla, la función retorna `np.nan`. Luego aplicamos esta función a cada valor en la columna 'HORA declarada' para obtener la hora del día en que ocurrieron los accidentes.


In [8]:
def convert_to_time(x, f):
    """
    Intenta convertir una entrada a un objeto de tiempo. Si la conversión falla, retorna np.nan.

    Parámetros:
    x : str
        La entrada a convertir a un objeto de tiempo.
    f: str
        El formato de la entrada. Ejemplo: '%H%M'

    Devuelve:
    datetime.time or np.nan
        Un objeto de tiempo si la conversión es exitosa, de lo contrario retorna np.nan.
    """
    try:
        return pd.to_datetime(x, format=f).time()
    except (ValueError, AttributeError):
        return np.nan  # Retorna np.nan si la conversión falla

# Usa una función lambda para pasar el argumento adicional a convert_to_time
df_accidentes['HORA declarada'] = df_accidentes['HORA declarada'].apply(lambda x: convert_to_time(x, '%H%M'))



## Vista Preliminar de los Datos

Echamos un vistazo a las primeras filas del dataframe para verificar las conversiones y tener una visión general de cómo se ven los datos después de las transformaciones realizadas hasta ahora.


In [9]:
df_accidentes.head()

fecha HORA declarada                                Ruta  \
0 1908-09-17       17:18:00                 Fort Myer, Virginia   
1 1909-09-07            NaN             Juvisy-sur-Orge, France   
2 1912-07-12       06:30:00           Atlantic City, New Jersey   
3 1913-08-06            NaN  Victoria, British Columbia, Canada   
4 1913-09-09       18:30:00                  Over the North Sea   

                 OperadOR flight_no          route                 ac_type  \
0    Military - U.S. Army       NaN  Demonstration        Wright Flyer III   
1                     NaN       NaN       Air show          Wright Byplane   
2    Military - U.S. Navy       NaN    Test flight               Dirigible   
3                 Private       NaN            NaN        Curtiss seaplane   
4  Military - German Navy       NaN            NaN  Zeppelin L-1 (airship)   

  registration cn_ln all_aboard PASAJEROS A BORDO crew_aboard  \
0          NaN     1          2                 1           1   
1          SC1   NaN          1                 0           1   
2          NaN   NaN          5                 0           5   
3          NaN   NaN          1                 0           1   
4          NaN   NaN         20               NaN         NaN   

  cantidad de fallecidos passenger_fatalities crew_fatalities ground  \
0                      1                    1               0      0   
1                      1                    0               0      0   
2                      5                    0               5      0   
3                      1                    0               1      0   
4                     14                  NaN             NaN      0   

                                             summary  
0  During a demonstration flight, a U.S. Army fly...  
1  Eugene Lefebvre was the first pilot to ever be...  
2  First U.S. dirigible Akron exploded just offsh...  
3  The first fatal airplane accident in Canada oc...  
4  The airship flew into a thunderstorm and encou...

## Descripción Estadística de los Datos
Utilizamos el método `describe` para obtener un resumen estadístico de los datos, lo que incluye la tendencia central, la dispersión y la forma de la distribución del conjunto de datos, excluyendo los valores `NaN`.


In [10]:
df_accidentes.describe()

fecha
count                           5008
mean   1971-05-14 09:57:13.226837072
min              1908-09-17 00:00:00
25%              1951-05-07 12:00:00
50%              1970-09-02 12:00:00
75%              1992-03-22 12:00:00
max              2021-07-06 00:00:00

## Categorización del Operador

Aquí, estamos intentando categorizar los operadores de las aeronaves en distintas categorías como 'Militar', 'Comercial', 'Privado', 'Correo', 'Desconocido', y 'Otro' basándonos en ciertas palabras clave. La función `categorize_operator` realiza esta tarea, y luego se aplica a la columna 'OperadOR'. También se realiza una exploración adicional en las categorías 'Desconocido' y 'Otro' para entender mejor estos grupos.


In [11]:
# Crear una nueva columna para las categorías
df_accidentes['Operator_Category'] = ''

# Definir las reglas de categorización
military_keywords = ['MILITARY', 'ARMY', 'NAVY', 'AIR FORCE', 'MARINE CORPS']
commercial_keywords = ['AIRLINES', 'AIRWAYS', 'LUFTHANSA', 'AEROFLOT', 'AIR FRANCE']
private_keywords = ['PRIVATE']
mail_keywords = ['MAIL', 'AERIAL MAIL']

def categorize_operator(operator):
    """
    Categoriza el operador de una aeronave en una de las siguientes categorías: 'Militar', 'Comercial', 'Privado', 'Correo', 'Desconocido', 'Otro'.

    Parámetros:
    operator : str
        El operador a categorizar.

    Devuelve:
    str
        Una cadena que indica la categoría del operador.
    """
    ...
 
    if pd.isna(operator):  # Verificar si operator es NaN
        return 'Desconocido'
    elif isinstance(operator, str):  # Verificar si operator es una string
        operator = operator.upper()  # Convertir a mayúsculas para comparación
        if any(keyword in operator for keyword in military_keywords):
            return 'Militar'
        elif any(keyword in operator for keyword in commercial_keywords):
            return 'Comercial'
        elif any(keyword in operator for keyword in private_keywords):
            return 'Privado'
        elif any(keyword in operator for keyword in mail_keywords):
            return 'Correo'
    return 'Otro'  # Retornar 'Otro' si operator no es una string o no coincide con ninguna categoría

# Aplicar la función a la columna 'OperadOR'
df_accidentes['Operator_Category'] = df_accidentes['OperadOR'].apply(categorize_operator)

# Para 'Desconocido'
desconocido_operadores_unicos = df_accidentes.loc[df_accidentes['Operator_Category'] == 'Desconocido', 'OperadOR'].unique()

# Para 'Otro'
otro_operadores_unicos = df_accidentes.loc[df_accidentes['Operator_Category'] == 'Otro', 'OperadOR'].unique()

# Si deseas ver los resultados, puedes imprimirlos:
print('Operadores Desconocidos Únicos:')
print(desconocido_operadores_unicos)
print('\nOperadores Otros Únicos:')
print(otro_operadores_unicos)


desconocido_operadores_unicos.sort()
otro_operadores_unicos.sort()
desconocido_operadores_unicos
np.savetxt('otro_operadores_unicos.txt', otro_operadores_unicos, fmt='%s')

# Contar el número total de registros en el dataset
total_registros = len(df_accidentes)

# Contar el número de registros categorizados como 'Otros'
df_otros = df_accidentes[df_accidentes['Operator_Category'] == 'Otro']
total_otros = len(df_otros)

# Calcular la proporción
proporcion_otros = (total_otros / total_registros) * 100

# Imprimir la proporción
print(f'La proporción de registros categorizados como "Otros" es: {proporcion_otros:.2f}%')


# Filtrar los registros categorizados como 'Otro'
otros_df = df_accidentes[df_accidentes['Operator_Category'] == 'Otro']

# Obtener un sample aleatorio de 500 registros
sample_otros = otros_df.sample(n=500, random_state=1)  # El parámetro random_state asegura reproducibilidad

# Exportar el sample a un archivo CSV

sample_otros['OperadOR'].to_csv('./data/sample_otros.csv', index=False)


Operadores Desconocidos Únicos:
[nan]

Operadores Otros Únicos:
['Wingfoot Air Express Goodyear Tire' 'Caproni Company'
 'Aircraft Transport and Travel' ... 'Sriwijaya Air' 'Soloy Helicopters'
 'Kamchatka Aviation Enterprise']
La proporción de registros categorizados como "Otros" es: 48.48%


### Extensión de Palabras Clave

Se extendieron las listas de palabras clave para mejorar la categorización, incluyendo más variaciones y nombres de operadores conocidos.


In [12]:

# Añadiendo más keywords y re-categorizando

# Militar:
military_keywords.extend(['ARMED FORCES', 'ROYAL AIR FORCE', 'AIR CORPS', 'AIR NATIONAL GUARD', 'COAST GUARD', 'MILITAIRE'])

# Comercial:
commercial_keywords.extend(['AVIATION', 'AVIANCA', 'AIRLINES', 'AIRLINE', 'AIRASIA', 'AIR INDIA', 'AIRWAYS', 'ALASKA', 'ALITALIA', 'AMERICAN AIRLINES', 'BRITISH AIRWAYS', 'CATHAY PACIFIC', 'DELTA', 'EMIRATES', 'ETIHAD', 'FRONTIER', 'JETBLUE', 'KLM', 'LUFTHANSA', 'QANTAS', 'RYANAIR', 'SOUTHWEST', 'SPIRIT', 'TURKISH AIRLINES', 'UNITED', 'VIRGIN', 'AIR CANADA', 'AEROMEXICO', 'AIR NEW ZEALAND', 'CHINA SOUTHERN', 'EASYJET', 'AIR BERLIN', 'SINGAPORE AIRLINES', 'AEROLINEAS', 'AIR EUROPA', 'AIR CHINA', 'LAN', 'TAM', 'VOLARIS', 'AIR TRANSPORT', 'TRANS WORLD', 'VARIG', 'VUELING', 'WIZZ AIR'])

# Privado:
private_keywords.extend(['CHARTER', 'EXECUTIVE', 'JET', 'TAXI', 'AERO', 'SERVICES', 'SERVICE', 'AIR TAXI', 'HELICOPTER', 'HELICOPTERS', 'AVIATION SERVICES'])

# Correo:
mail_keywords.extend(['EXPRESS', 'CARGO', 'FREIGHT', 'COURIER', 'LOGISTICS', 'PARCEL', 'SHIPPING', 'TRANSPORT', 'AIR CARGO', 'CARGO AIRLINE', 'POSTAL', 'POSTALE'])


df_accidentes['Operator_Category'] = df_accidentes['OperadOR'].apply(categorize_operator)

# Para 'Desconocido'
desconocido_operadores_unicos = df_accidentes.loc[df_accidentes['Operator_Category'] == 'Desconocido', 'OperadOR'].unique()

# Para 'Otro'
otro_operadores_unicos = df_accidentes.loc[df_accidentes['Operator_Category'] == 'Otro', 'OperadOR'].unique()

print('Operadores Desconocidos Únicos:')
print(desconocido_operadores_unicos)
print('\nOperadores Otros Únicos:')
print(otro_operadores_unicos)


desconocido_operadores_unicos.sort()
otro_operadores_unicos.sort()

# Contar el número total de registros en el dataset
total_registros = len(df_accidentes)

# Contar el número de registros categorizados como 'Otros'
df_otros = df_accidentes[df_accidentes['Operator_Category'] == 'Otro']
total_otros = len(df_otros)

# Calcular la proporción
proporcion_otros = (total_otros / total_registros) * 100

# Imprimir la proporción
print(f'La proporción de registros categorizados como "Otros" es: {proporcion_otros:.2f}%')

# Filtrar los registros categorizados como 'Otro'
otros_df = df_accidentes[df_accidentes['Operator_Category'] == 'Otro']

# Obtener un sample aleatorio de 500 registros
sample_otros = otros_df.sample(n=500, random_state=1)
print(sample_otros['OperadOR'])

# Exportar el sample a un archivo CSV
sample_otros['OperadOR'].to_csv('./data/sample_otros2.csv', index=False)

Operadores Desconocidos Únicos:
[nan]

Operadores Otros Únicos:
['Caproni Company' 'Compañia Colombiana de Navegación Aérea' 'By Air'
 'Franco-Roumaine' 'Cie des Messageries Aeriennes'
 'Compagnie Franco-Roumaine de Navigaation Aerienne' "Amee de l'Air"
 'Air Union' 'Campagnie France Roumaine' 'CCCP' 'SCADTA' 'Zakavia'
 'Lignes Aeriennes Latecoere' 'CIDNA'
 'Compagnie Internationale de Navigation Aérienne' 'Fokker'
 'Varney Air Lines' 'Continental Air Lines' 'Syndicato Condor' 'Mexicana'
 'MALERT' 'Ukvozduchput' 'Associated Aviators' 'Skyways'
 'S.A.M. Società Aerea Mediterranea' 'Air Orient' 'Walcot Air Line'
 'Sabena' 'Wings Ltd' 'Embry Riddle Company' 'Dominion Air Lines'
 'Trans Continental and Western Air' 'NY, Phil., Washington AW'
 'Century Pacific Lines' 'Century Air Lines' 'Panagra' 'Eurasia'
 'Palwaukee' 'Kalinin' 'Boeing Aircraft Company' 'Swissair'
 'Cubana de Aviacion' 'Deruluft' 'Misrair' "Gor'ky Eskadril'ya"
 'Servicio Aereo Columbiano / SCADTA' 'Fuerza Aerea Colombiana'

## Conversión de Tipos de Datos

Primero, estamos convirtiendo varias columnas a un tipo de datos entero (`Int64`) para facilitar el análisis numérico posterior.

In [13]:
# Lista de columnas a convertir
columns_to_convert = [
    'all_aboard', 'PASAJEROS A BORDO', 'crew_aboard', 
    'cantidad de fallecidos', 'passenger_fatalities', 
    'crew_fatalities', 'ground'
]

# Convertir cada columna a Int64
for column in columns_to_convert:
    df_accidentes[column] = df_accidentes[column].astype('Int64', errors='raise')

# Verificar los cambios
print(df_accidentes[columns_to_convert].dtypes)



all_aboard                Int64
PASAJEROS A BORDO         Int64
crew_aboard               Int64
cantidad de fallecidos    Int64
passenger_fatalities      Int64
crew_fatalities           Int64
ground                    Int64
dtype: object


Se revisan los datos y tipos de las columnas 'fecha' y 'HORA declarada' para asegurarse de que la conversión se haya realizado correctamente.

In [14]:
df_accidentes[['fecha', 'HORA declarada']].info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5008 entries, 0 to 5007
Data columns (total 2 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   fecha           5008 non-null   datetime64[ns]
 1   HORA declarada  3287 non-null   object        
dtypes: datetime64[ns](1), object(1)
memory usage: 78.4+ KB


### Conversión y Limpieza de la Hora
Se extrae la información de hora de la columna 'HORA declarada', se crea una nueva columna 'hora' y se elimina la columna original 'HORA declarada'.


In [15]:
df_accidentes['hora'] = pd.to_datetime(df_accidentes['HORA declarada'], format='%H:%M:%S', errors='coerce').dt.time
df_accidentes['hora'] = df_accidentes['hora'].apply(lambda x: None if pd.isna(x) else x)
df_accidentes.drop(columns=['HORA declarada'], inplace=True)

df_accidentes.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5008 entries, 0 to 5007
Data columns (total 18 columns):
 #   Column                  Non-Null Count  Dtype         
---  ------                  --------------  -----         
 0   fecha                   5008 non-null   datetime64[ns]
 1   Ruta                    5003 non-null   object        
 2   OperadOR                4998 non-null   object        
 3   flight_no               1326 non-null   object        
 4   route                   4245 non-null   object        
 5   ac_type                 4995 non-null   object        
 6   registration            4736 non-null   object        
 7   cn_ln                   4341 non-null   object        
 8   all_aboard              4991 non-null   Int64         
 9   PASAJEROS A BORDO       4787 non-null   Int64         
 10  crew_aboard             4789 non-null   Int64         
 11  cantidad de fallecidos  5000 non-null   Int64         
 12  passenger_fatalities    4773 non-null   Int64   

## Llenado de Valores Nulos
Se llenan los valores nulos en varias columnas con cadenas vacías para evitar posibles errores en análisis futuros.

In [16]:
df_accidentes.fillna({'Ruta': '', 'OperadOR': '', 'flight_no': '', 'route': '', 'ac_type': '', 'registration': '', 'cn_ln': '', 'summary': ''}, inplace=True)


## Verificación de Tipos de Datos

Se verifica el tipo de datos de cada elemento en el DataFrame y se muestran los tipos únicos por columna.

In [17]:
# Mostrar el tipo de dato de cada elemento
df_types = df_accidentes.applymap(type)

# Ver los tipos únicos por columna
unique_types = df_types.apply(lambda x: x.unique())

# Mostrar los tipos únicos por columna
display(unique_types)

fecha                     [<class 'pandas._libs.tslibs.timestamps.Timest...
Ruta                                                        [<class 'str'>]
OperadOR                                                    [<class 'str'>]
flight_no                                                   [<class 'str'>]
route                                                       [<class 'str'>]
ac_type                                                     [<class 'str'>]
registration                                                [<class 'str'>]
cn_ln                                                       [<class 'str'>]
all_aboard                [<class 'int'>, <class 'pandas._libs.missing.N...
PASAJEROS A BORDO         [<class 'int'>, <class 'pandas._libs.missing.N...
crew_aboard               [<class 'int'>, <class 'pandas._libs.missing.N...
cantidad de fallecidos    [<class 'int'>, <class 'pandas._libs.missing.N...
passenger_fatalities      [<class 'int'>, <class 'pandas._libs.missing.N...
crew_fatalit

Se realiza una revisión final de los tipos de datos en el DataFrame.

In [18]:
print(df_accidentes.dtypes)

fecha                     datetime64[ns]
Ruta                              object
OperadOR                          object
flight_no                         object
route                             object
ac_type                           object
registration                      object
cn_ln                             object
all_aboard                         Int64
PASAJEROS A BORDO                  Int64
crew_aboard                        Int64
cantidad de fallecidos             Int64
passenger_fatalities               Int64
crew_fatalities                    Int64
ground                             Int64
summary                           object
Operator_Category                 object
hora                              object
dtype: object


## Exploración de Columnas 'route' y 'Ruta'

Se exploran las columnas 'route' y 'Ruta' para entender mejor la información que contienen.


In [19]:
df_accidentes[['route','Ruta']].tail(10)

route                        Ruta
4998               Dubai - Calicut              Calicut, India
4999                    Juba - Wau           Juba, South Sudan
5000                      Training       Near Chuguev, Ukraine
5001           Jakarta - Pontianak     Near Jakarta, Indonesia
5002                  Pieri - Yuai                Pieri, Sudan
5003           Sightseeing Charter          Near Butte, Alaska
5004                                      Near Kaduna, Nigeria
5005          Naypyidaw - Anisakan  Near Pyin Oo Lwin, Myanmar
5006  Cagayan de Oro-Lumbia - Jolo  Patikul, Sulu, Philippines
5007        Petropavlovsk - Palana              Palana, Russia

In [20]:
for index, row in df_accidentes.head().iterrows():
    print(f"Index: {index}, Route: {row['route']}, Ruta: {row['Ruta']}, Summary: {row['summary']}\n")

for index, row in df_accidentes.tail().iterrows():
    print(f"Index: {index}, Route: {row['route']}, Ruta: {row['Ruta']}, Summary: {row['summary']}\n")


Index: 0, Route: Demonstration, Ruta: Fort Myer, Virginia, Summary: During a demonstration flight, a U.S. Army flyer flown by Orville Wright nose-dived into the ground from a height of approximately 75 feet, killing Lt. Thomas E. Selfridge, 26, who was a passenger. This was the first recorded airplane fatality in history.  One of two propellers separated in flight, tearing loose the wires bracing the rudder and causing the loss of control of the aircraft.  Orville Wright suffered broken ribs, pelvis and a leg.  Selfridge suffered a crushed skull and died a short time later.

Index: 1, Route: Air show, Ruta: Juvisy-sur-Orge, France, Summary: Eugene Lefebvre was the first pilot to ever be killed in an air accident, after his controls jambed while flying in an air show.

Index: 2, Route: Test flight, Ruta: Atlantic City, New Jersey, Summary: First U.S. dirigible Akron exploded just offshore at an altitude of 1,000 ft. during a test flight.

Index: 3, Route: , Ruta: Victoria, British Colum

## Reordenamiento de Columnas
Se define un nuevo orden para las columnas del DataFrame para una mejor organización y se verifica el resultado final.


In [21]:
# Definir el nuevo orden de las columnas
nuevo_orden = [
    'fecha', 'hora', 'OperadOR', 'flight_no', 'route', 'Ruta',
    'ac_type', 'registration', 'cn_ln', 
    'all_aboard', 'PASAJEROS A BORDO', 'crew_aboard',
    'cantidad de fallecidos', 'passenger_fatalities', 'crew_fatalities',
    'ground', 'summary'
]

# Reordenar las columnas
df_accidentes = df_accidentes.loc[:, nuevo_orden]

# Verificar el nuevo orden de las columnas
display(df_accidentes.head())

fecha      hora                OperadOR flight_no          route  \
0 1908-09-17  17:18:00    Military - U.S. Army            Demonstration   
1 1909-09-07      None                                         Air show   
2 1912-07-12  06:30:00    Military - U.S. Navy              Test flight   
3 1913-08-06      None                 Private                            
4 1913-09-09  18:30:00  Military - German Navy                            

                                 Ruta                 ac_type registration  \
0                 Fort Myer, Virginia        Wright Flyer III                
1             Juvisy-sur-Orge, France          Wright Byplane          SC1   
2           Atlantic City, New Jersey               Dirigible                
3  Victoria, British Columbia, Canada        Curtiss seaplane                
4                  Over the North Sea  Zeppelin L-1 (airship)                

  cn_ln  all_aboard  PASAJEROS A BORDO  crew_aboard  cantidad de fallecidos  \
0     1           2                  1            1                       1   
1                 1                  0            1                       1   
2                 5                  0            5                       5   
3                 1                  0            1                       1   
4                20               <NA>         <NA>                      14   

   passenger_fatalities  crew_fatalities  ground  \
0                     1                0       0   
1                     0                0       0   
2                     0                5       0   
3                     0                1       0   
4                  <NA>             <NA>       0   

                                             summary  
0  During a demonstration flight, a U.S. Army fly...  
1  Eugene Lefebvre was the first pilot to ever be...  
2  First U.S. dirigible Akron exploded just offsh...  
3  The first fatal airplane accident in Canada oc...  
4  The airship flew into a thunderstorm and encou...

## Renombrando Columnas

Se renombran las columnas del DataFrame para tener nombres más descriptivos y en inglés, facilitando el entendimiento y la manipulación de los datos en futuros análisis.

In [22]:
df_accidentes = df_accidentes.rename(columns={
    'fecha': 'Date',
    'Ruta': 'Location_or_Route',
    'OperadOR': 'Operator',
    'flight_no': 'Flight_Number',
    'route': 'Route',
    'ac_type': 'Aircraft_Type',
    'registration': 'Aircraft_Registration',
    'cn_ln': 'Construction_Number_or_Line_Number',
    'all_aboard': 'Total_Aboard',
    'PASAJEROS A BORDO': 'Passengers_Aboard',  
    'crew_aboard': 'Crew_Aboard',
    'cantidad de fallecidos': 'Total_Fatalities',
    'passenger_fatalities': 'Passenger_Fatalities',
    'crew_fatalities': 'Crew_Fatalities',
    'ground': 'Ground_Fatalities',
    'summary': 'Accident_Summary',
    'hora': 'Time'
})

# Verificar los cambios
print(df_accidentes.columns)


Index(['Date', 'Time', 'Operator', 'Flight_Number', 'Route',
       'Location_or_Route', 'Aircraft_Type', 'Aircraft_Registration',
       'Construction_Number_or_Line_Number', 'Total_Aboard',
       'Passengers_Aboard', 'Crew_Aboard', 'Total_Fatalities',
       'Passenger_Fatalities', 'Crew_Fatalities', 'Ground_Fatalities',
       'Accident_Summary'],
      dtype='object')


## Verificación de Coincidencia de Datos
Se verifica si la suma de pasajeros y tripulación a bordo coincide con el total registrado en la columna 'Total_Aboard'.


In [23]:
check = df_accidentes['Total_Aboard'].eq(df_accidentes['Passengers_Aboard'] + df_accidentes['Crew_Aboard']).all()

if check:
    print("Las columnas coinciden en todas las filas.")
else:
    print("Las columnas no coinciden en todas las filas.")


Las columnas no coinciden en todas las filas.


### Identificación de Discrepancias

Se identifican y muestran las filas donde no coinciden los datos de personas a bordo y fatalidades.


In [24]:
# Cuenta el número de filas donde las columnas no coinciden
mismatch_count = (~df_accidentes['Total_Aboard'].eq(df_accidentes['Passengers_Aboard'] + df_accidentes['Crew_Aboard'])).sum()

print(f'Número de filas donde las columnas no coinciden: {mismatch_count}')


Número de filas donde las columnas no coinciden: 31


In [25]:
# Encuentra las filas donde las columnas no coinciden
mismatch_rows = df_accidentes.loc[~df_accidentes['Total_Aboard'].eq(df_accidentes['Passengers_Aboard'] + df_accidentes['Crew_Aboard'])]

# Mostrar las filas donde las columnas no coinciden
mismatch_rows[['Total_Aboard', 'Passengers_Aboard', 'Crew_Aboard', 'Accident_Summary']].to_csv('./data/mismatch_rows.csv')


In [26]:
mismatch_rows[['Total_Aboard', 'Passengers_Aboard', 'Crew_Aboard']]

Total_Aboard  Passengers_Aboard  Crew_Aboard
30               0                  0            1
32               1                  1            1
39               1                  1            1
55               2                  0            0
120              0                  0            2
213              3                  0            2
495              2                  0            0
498              3                  0            0
1121             0                  1            1
1170             4                  0            2
1346            21                 19            5
1399            20                 16           11
1750            28                 30            2
2203            11                 11            2
2318            46                 39            6
2423             1                  0            4
2446             9                  9            2
2460            11                 32            6
2639           108                108            8
2680            61                 55            8
2689            85                 78            8
2843           124                104           10
2899            21                 17            3
3004            13                  9            5
3038           178                155           13
3109            11                  2            7
3196           285                270           25
4617            12                 10            4
4706             3                  3            2
4831             5                  3            3
4894            19                 21            2

In [27]:
# Encuentra las filas donde las columnas de fatalidades no coinciden
mismatch_fatalities_rows = df_accidentes.loc[~df_accidentes['Total_Fatalities'].eq(
    df_accidentes['Passenger_Fatalities'] + df_accidentes['Crew_Fatalities'] 
    # + df_accidentes['Ground_Fatalities']
    )]

# Contar el número de filas donde las columnas de fatalidades no coinciden
mismatch_fatalities_count = len(mismatch_fatalities_rows)
print(f'Número de filas donde las columnas de fatalidades no coinciden: {mismatch_fatalities_count}')

# Mostrar las filas donde las columnas de fatalidades no coinciden
display(mismatch_fatalities_rows[['Total_Fatalities', 'Passenger_Fatalities', 'Crew_Fatalities', 'Ground_Fatalities']])


# TODO comparar ctotal crew y passangers con fallecidos. Cantidad de sobreregistros o subregistros 

Número de filas donde las columnas de fatalidades no coinciden: 41


Total_Fatalities  Passenger_Fatalities  Crew_Fatalities  \
1                    1                     0                0   
32                   1                     1                1   
39                   1                     1                1   
55                   2                     0                0   
120                  0                     0                2   
178                  2                     7                2   
186                  4                     3                2   
361                  0                     0                2   
381                  1                     3                0   
402                 12                     9                1   
495                  2                     0                0   
498                  3                     0                0   
504                  1                     5                1   
691                 18                    18                3   
698                 13                    12                3   
943                 11                     8                2   
987                 41                    38                4   
1006                 9                     3                4   
1121                 0                     1                1   
1346                21                    19                5   
1399                20                    16               11   
1659                 7                     0                6   
2203                11                    11                2   
2446                 9                     9                2   
2563                 9                     6                2   
2680                61                    55                8   
2717                13                    11                5   
2781                24                   213                3   
2884                 3                     3                1   
3038               178                   155               13   
3045                 4                     8                1   
3109                11                     2                7   
3145                60                    75                5   
3227                15                    98                6   
3230                33                    37                6   
3397                16                    14                1   
3559                12                    10                1   
4617                12                    10                4   
4706                 3                     3                2   
4728                 4                     0                3   
4839                 0                     0                4   

      Ground_Fatalities  
1                     0  
32                    0  
39                    0  
55                    0  
120                   0  
178                   0  
186                   0  
361                  15  
381                   0  
402                   0  
495                   0  
498                   0  
504                   0  
691                   0  
698                   0  
943                   0  
987                   0  
1006                  0  
1121                 14  
1346                  0  
1399                  0  
1659                  1  
2203                  0  
2446                  0  
2563                  0  
2680                  0  
2717                  0  
2781                  0  
2884                  0  
3038                  0  
3045                  0  
3109                  0  
3145                 20  
3227                  0  
3230                  0  
3397                  1  
3559                  0  
4617                  0  
4706                  0  
4728               <NA>  
4839                 12

### Identificación de Discrepancias (Función)
Se define una función para identificar las discrepancias entre las columnas 'Aboard' y 'Fatalities', y se aplica esta función al DataFrame.

In [28]:
def identify_discrepancy(row):
    """
    Identifica discrepancias en las columnas 'Aboard' y 'Fatalities' de una fila dada.

    Parámetros:
    row : pandas.Series
        La fila del DataFrame a verificar.

    Devuelve:
    str
        Una cadena que indica el tipo de discrepancia ('Both', 'Aboard', 'Fatalities', 'None').
    """
    ...

    aboard_discrepancy = (
        pd.isna(row['Total_Aboard']) or
        pd.isna(row['Passengers_Aboard']) or
        pd.isna(row['Crew_Aboard']) or
        row['Total_Aboard'] != (row['Passengers_Aboard'] + row['Crew_Aboard'])
    )

    fatalities_discrepancy = (
        pd.isna(row['Total_Fatalities']) or
        pd.isna(row['Passenger_Fatalities']) or
        pd.isna(row['Crew_Fatalities']) or
        pd.isna(row['Ground_Fatalities']) or
        row['Total_Fatalities'] != (row['Passenger_Fatalities'] + row['Crew_Fatalities'] + row['Ground_Fatalities'])
    )

    if aboard_discrepancy and fatalities_discrepancy:
        return 'Both'
    elif aboard_discrepancy:
        return 'Aboard'
    elif fatalities_discrepancy:
        return 'Fatalities'
    else:
        return 'None'

# Aplicar la función a cada fila del DataFrame
df_accidentes['Aboard_or_Fatalities_Discrepancy'] = df_accidentes.apply(identify_discrepancy, axis=1).astype('category')

discrepancy_cols = ['Total_Aboard', 'Passengers_Aboard', 'Crew_Aboard', 'Total_Fatalities', 'Passenger_Fatalities', 'Crew_Fatalities', 'Ground_Fatalities', 'Aboard_or_Fatalities_Discrepancy']

# Ver los primeros registros para verificar los resultados
display(df_accidentes[discrepancy_cols].head())


Total_Aboard  Passengers_Aboard  Crew_Aboard  Total_Fatalities  \
0             2                  1            1                 1   
1             1                  0            1                 1   
2             5                  0            5                 5   
3             1                  0            1                 1   
4            20               <NA>         <NA>                14   

   Passenger_Fatalities  Crew_Fatalities  Ground_Fatalities  \
0                     1                0                  0   
1                     0                0                  0   
2                     0                5                  0   
3                     0                1                  0   
4                  <NA>             <NA>                  0   

  Aboard_or_Fatalities_Discrepancy  
0                             None  
1                       Fatalities  
2                             None  
3                             None  
4                             Both

### Exportación de Filas con Discrepancias

Se filtran y exportan las filas que presentan discrepancias en los datos de personas a bordo o fatalidades a un archivo CSV para un análisis más detallado.



In [29]:
# Filtrar las filas donde la columna 'Aboard_or_Fatalities_Discrepancy' es diferente de 'None'
discrepancy_rows = df_accidentes[df_accidentes['Aboard_or_Fatalities_Discrepancy'] != 'None']

# Mostrar las filas con discrepancias
display(discrepancy_rows)
discrepancy_rows[discrepancy_cols].to_csv('./data/Aboard_or_Fatalities_Discrepancy.csv')

Date      Time                         Operator Flight_Number  \
1    1909-09-07      None                                                  
4    1913-09-09  18:30:00           Military - German Navy                 
5    1913-10-17  10:30:00           Military - German Navy                 
7    1915-09-03  15:20:00           Military - German Navy                 
8    1916-07-28      None           Military - German Army                 
...         ...       ...                              ...           ...   
4988 2019-07-30  02:00:00         Military - Pakistan Army                 
4991 2019-11-24  09:15:00                   Busy Bee Congo                 
4993 2020-01-02      None               Sudanese Air Force                 
4997 2020-05-22  14:40:00   Pakistan International Airline        PK8303   
5006 2021-07-04      None  Military - Philippine Air Force                 

                             Route                   Location_or_Route  \
1                         Air show             Juvisy-sur-Orge, France   
4                                                   Over the North Sea   
5                                           Near Johannisthal, Germany   
7                                                Off Cuxhaven, Germany   
8                                                Near Jambol, Bulgeria   
...                            ...                                 ...   
4988                      Training                   Rawalpindi, India   
4991                   Goma - Beni  Goma, Democratic Republic of Congo   
4993            Geneina - Khartoum                      Geneina, Sudan   
4997              Lahore - Karachi                   Karachi, Pakistan   
5006  Cagayan de Oro-Lumbia - Jolo          Patikul, Sulu, Philippines   

                      Aircraft_Type Aircraft_Registration  \
1                    Wright Byplane                   SC1   
4            Zeppelin L-1 (airship)                         
5            Zeppelin L-2 (airship)                         
7           Zeppelin L-10 (airship)                         
8     Schutte-Lanz S-L-10 (airship)                         
...                             ...                   ...   
4988       Beechcraft B300 King Air                   766   
4991                Dornier 228-201                9S-GNH   
4993                 Antonov An12-A                         
4997                Airbus A320-214                AP-BLD   
5006       Lockheed C-130H Hercules                  5125   

     Construction_Number_or_Line_Number  Total_Aboard  Passengers_Aboard  \
1                                                   1                  0   
4                                                  20               <NA>   
5                                                  28               <NA>   
7                                                  19               <NA>   
8                                                  20               <NA>   
...                                 ...           ...                ...   
4988                               B766             5                  0   
4991                               8030            19                 17   
4993                            2340606            18                  9   
4997                               2274            99                 91   
5006                               5125            96                 88   

      Crew_Aboard  Total_Fatalities  Passenger_Fatalities  Crew_Fatalities  \
1               1                 1                     0                0   
4            <NA>                14                  <NA>             <NA>   
5            <NA>                28                  <NA>             <NA>   
7            <NA>                19                  <NA>             <NA>   
8            <NA>                20                  <NA>             <NA>   
...           ...               ...                   ...              ...   
4988            5

## Verificación de Duplicados
Se verifica la presencia de filas duplicadas en el DataFrame.


In [30]:
duplicate_rows = df_accidentes[df_accidentes.duplicated()]
print(f'Número de registros duplicados: {duplicate_rows.shape[0]}')


Número de registros duplicados: 0


## Verificación de Datos Faltantes
Se verifica la presencia de datos faltantes en el DataFrame, y se reemplazan las cadenas vacías por NaN.

In [31]:
missing_data = df_accidentes.isnull().sum()
print(missing_data)


Date                                     0
Time                                  1721
Operator                                 0
Flight_Number                            0
Route                                    0
Location_or_Route                        0
Aircraft_Type                            0
Aircraft_Registration                    0
Construction_Number_or_Line_Number       0
Total_Aboard                            17
Passengers_Aboard                      221
Crew_Aboard                            219
Total_Fatalities                         8
Passenger_Fatalities                   235
Crew_Fatalities                        235
Ground_Fatalities                       44
Accident_Summary                         0
Aboard_or_Fatalities_Discrepancy         0
dtype: int64


In [32]:
df_accidentes.replace('', np.nan, inplace=True)
missing_data = df_accidentes.isnull().sum()
print(missing_data)

Date                                     0
Time                                  1721
Operator                                10
Flight_Number                         3682
Route                                  763
Location_or_Route                        5
Aircraft_Type                           13
Aircraft_Registration                  272
Construction_Number_or_Line_Number     667
Total_Aboard                            17
Passengers_Aboard                      221
Crew_Aboard                            219
Total_Fatalities                         8
Passenger_Fatalities                   235
Crew_Fatalities                        235
Ground_Fatalities                       44
Accident_Summary                        59
Aboard_or_Fatalities_Discrepancy         0
dtype: int64


In [33]:
unique_count = df_accidentes['Aircraft_Registration'].nunique()
print("Unique cases:", unique_count)


Unique cases: 4700


In [34]:
df_accidentes['Aircraft_Registration'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 5008 entries, 0 to 5007
Series name: Aircraft_Registration
Non-Null Count  Dtype 
--------------  ----- 
4736 non-null   object
dtypes: object(1)
memory usage: 39.3+ KB


In [35]:
# Obtener la frecuencia de cada valor único en la columna 'Aircraft_Registration'
value_counts = df_accidentes['Aircraft_Registration'].value_counts()

# Filtrar sólo los valores que aparecen más de una vez
repeated_values = value_counts[value_counts > 1]

# Mostrar los valores repetidos y su frecuencia
print(repeated_values)


Aircraft_Registration
49            3
F-BBDM        2
TC-72         2
NC14272       2
N91303        2
N37741        2
RF-76801      2
ZRS-4         2
F-FHMY        2
19            2
YR-PAF        2
2             2
CCCP-46724    2
SP-AYD        2
223           2
CCCP-45012    2
I-BAUS        2
CCCP-09303    2
101           2
G-ADUZ        2
VH-ABB        2
53            2
XA-GOT        2
G-AEUH        2
F-AIUJ        2
82            2
32            2
CF-TCL        2
77            2
SU-AFK        2
44-77577      2
204           2
OK-MCT        2
12406         2
F-AHEQ        2
Name: count, dtype: int64


In [36]:
# Encontrar las filas donde la columna 'Aircraft_Registration' tiene valores duplicados
duplicated_rows = df_accidentes[df_accidentes.duplicated(subset='Aircraft_Registration', keep=False)]

# Ordenar las filas duplicadas por 'Aircraft_Registration' para ver los duplicados juntos
sorted_duplicated_rows = duplicated_rows.sort_values(by='Aircraft_Registration')

# Mostrar las filas duplicadas
display(sorted_duplicated_rows)


Date      Time                                    Operator  \
4760 2010-04-10  10:41:00                 Military - Polish Air Force   
745  1944-10-07      None         China National Aviation Corporation   
681  1943-06-14  06:00:00             Military - U.S. Army Air Forces   
680  1943-06-08  00:55:00                          Military - US Navy   
3385 1986-05-18  08:30:00            Military - French Naval Aviation   
...         ...       ...                                         ...   
4875 2013-11-09  10:30:00                  Military - Indonesian Army   
4894 2014-07-07  07:50:00  Military - Vietnam People's Army Air Force   
4902 2014-10-04  01:56:00                           Air Evac Lifeteam   
4905 2015-01-18      None                            Syrian Air Force   
4993 2020-01-02      None                          Sudanese Air Force   

     Flight_Number                             Route  \
4760       PLF 101  Warsaw, Poland - Smolensk Russia   
745            NaN                    Dinjan - Suifu   
681            NaN             Mackay - Port Moresby   
680            NaN                   Noumea - Sydney   
3385           NaN                               NaN   
...            ...                               ...   
4875           NaN                 Tarakan - Malinau   
4894           NaN                          Training   
4902           NaN   Waurika, OK - Wichita Falls, TX   
4905           NaN         Damascus - Abu Adh Dhuhur   
4993           NaN                Geneina - Khartoum   

                        Location_or_Route                 Aircraft_Type  \
4760                     Smolensk, Russia                  Tupolev 154M   
745                    Near Sadiya, India                  Douglas C-47   
681           Near Mackay, OLD, Australia         B-17C Flying Fortress   
680                Noumea,  New Caledonia  Douglas C-47 Skytrain (DC-3)   
3385                   Djibouti, Djibouti   Dassault Breguet Atlantique   
...                                   ...                           ...   
4875   Pujungan, Malinau district, Borneo                 Mil- Mi-17B-5   
4894         Thach That district, Vietnam                    Mil Mi-171   
4902                 Wichita Falls, Texas                     Bell 206L   
4905  Near Abu adh Dhuhur Air Base, Syria                 Antonov An-26   
4993                       Geneina, Sudan                Antonov An12-A   

     Aircraft_Registration Construction_Number_or_Line_Number  Total_Aboard  \
4760                   101                             90A837            96   
745                    101                                NaN             3   
681                  12406                               2072            41   
680                  12406                               9178            23   
3385                    19                                 19            19   
...                    ...                                ...           ...   
4875                   NaN                                NaN            21   
4894                   NaN                                NaN            19   
4902                   NaN                                NaN             4   
4905                   NaN                                NaN            37   
4993                   NaN                            2340606            18   

      Passengers_Aboard  Crew_Aboard  Total_Fatalities  Passenger_Fatalities  \
4760                 88            8                96                    88   
745                   0            3                 3                     0   
681                  35            6                40                    34   
680                   3           20                23                     3   
3385                 14            5                19                    14   
...                 ...          ...               ...                   ...   
4875                 13            8               

In [37]:
# TODO revisar 36 repetidos en Aircraft_Registration

### Filtrado de Filas con Valores Faltantes
Se crea una función para filtrar filas con un número mínimo de valores faltantes y se aplica al DataFrame.

In [38]:
def filtrar_filas_con_valores_faltantes(df, min_valores_faltantes):
    """
    Esta función filtra las filas de un DataFrame de pandas que tienen al menos un número mínimo de valores faltantes.

    Parámetros:
    df (pandas.DataFrame): El DataFrame a filtrar.
    min_valores_faltantes (int): El número mínimo de valores faltantes que debe tener una fila para ser incluida en el DataFrame resultante.

    Devuelve:
    pandas.DataFrame: Un nuevo DataFrame que solo incluye las filas con al menos min_valores_faltantes valores faltantes.
    """
    return df[df.isnull().sum(axis=1) >= min_valores_faltantes]


In [39]:
filtrar_filas_con_valores_faltantes(df_accidentes, 13)

Date  Time                             Operator Flight_Number Route  \
103 1925-09-07  None                                CIDNA           NaN   NaN   
347 1934-08-10  None  China National Aviation Corporation           NaN   NaN   
754 1944-11-09  None       Military - U.S. Army Air Corps           NaN   NaN   

    Location_or_Route   Aircraft_Type Aircraft_Registration  \
103      Toul, France         Spad 33                   NaN   
347     Ningbo, China  Sikorsky S-38B                   NaN   
754   Seljord, Norway             NaN              42-52196   

    Construction_Number_or_Line_Number  Total_Aboard  Passengers_Aboard  \
103                                NaN          <NA>               <NA>   
347                                NaN          <NA>               <NA>   
754                                NaN          <NA>               <NA>   

     Crew_Aboard  Total_Fatalities  Passenger_Fatalities  Crew_Fatalities  \
103         <NA>              <NA>                  <NA>             <NA>   
347         <NA>              <NA>                  <NA>             <NA>   
754         <NA>              <NA>                  <NA>             <NA>   

     Ground_Fatalities Accident_Summary Aboard_or_Fatalities_Discrepancy  
103               <NA>              NaN                             Both  
347               <NA>              NaN                             Both  
754               <NA>              NaN                             Both

In [41]:
df_accidentes.describe()


Date  Total_Aboard  Passengers_Aboard  \
count                           5008        4991.0             4787.0   
mean   1971-05-14 09:57:13.226837072     31.121218          26.877376   
min              1908-09-17 00:00:00           0.0                0.0   
25%              1951-05-07 12:00:00           7.0                3.0   
50%              1970-09-02 12:00:00          16.0               12.0   
75%              1992-03-22 12:00:00          35.0               30.0   
max              2021-07-06 00:00:00         644.0              614.0   
std                              NaN     45.479965          44.035342   

       Crew_Aboard  Total_Fatalities  Passenger_Fatalities  Crew_Fatalities  \
count       4789.0            5000.0                4773.0           4773.0   
mean      4.519524            22.294             18.940708         3.587262   
min            0.0               0.0                   0.0              0.0   
25%            2.0               4.0                   1.0              2.0   
50%            4.0              11.0                   7.0              3.0   
75%            6.0              25.0                  21.0              5.0   
max           83.0             583.0                 560.0             43.0   
std       3.758072         35.000385              34.06519         3.177315   

       Ground_Fatalities         Year  
count             4964.0  5008.000000  
mean            1.718372  1970.851637  
min                  0.0  1908.000000  
25%                  0.0  1951.000000  
50%                  0.0  1970.000000  
75%                  0.0  1992.000000  
max               2750.0  2021.000000  
std            55.495544    24.703696

## Exploración de la Columna 'Route'
Se explora la columna 'Route' para entender mejor la información que contiene.

In [42]:
Route  = df_accidentes[['Route']].apply(lambda x: x.unique())

# Mostrar los tipos únicos de la columna
display(Route)

Route
0                    Demonstration
1                         Air show
2                      Test flight
3                              NaN
4                          Shuttle
...                            ...
3833                  Pieri - Yuai
3834           Sightseeing Charter
3835          Naypyidaw - Anisakan
3836  Cagayan de Oro-Lumbia - Jolo
3837        Petropavlovsk - Palana

[3838 rows x 1 columns]

Descubri que hay caracteres de control como \r y \t en el archivo csv original...

In [43]:
fila_4542 = df_accidentes.loc[4542]

# Mostrar la fila
print(fila_4542)


Date                                                                2005-02-22 00:00:00
Time                                                                           07:15:00
Operator                                                     Indonesian National Police
Flight_Number                                                                       NaN
Route                                                                  Jayapura - Sarmi
Location_or_Route                            Off Sarmi, Indonesia\r\t\rSarmi, Indonesia
Aircraft_Type                                                          CASA 212 Aviocar
Aircraft_Registration                                                    P-2032\rP-2032
Construction_Number_or_Line_Number                                                  NaN
Total_Aboard                                                                         18
Passengers_Aboard                                                                    14
Crew_Aboard                     

In [44]:
import re

def has_control_char(value):
    """ Verifica si una cadena contiene caracteres de control \r, \n o \t """
    if pd.isna(value) or not isinstance(value, str):
        return False  # Retorna False si el valor es NaN o no es una cadena
    return bool(re.search(r'[\r\n\t]', value))  # Retorna True si encuentra un caracter de control

# Seleccionar solo las columnas de texto (excluyendo 'Date' y 'Time')
text_columns = df_accidentes.drop(columns=['Date', 'Time']).select_dtypes(include='object')

# Aplicar la función a cada columna de texto
control_char_check = text_columns.applymap(has_control_char)

# Identificar las filas que contienen al menos un caracter de control
rows_with_control_char = control_char_check.any(axis=1)

# Filtrar el DataFrame original para mostrar solo las filas con caracteres de control
df_control_char_rows = df_accidentes[rows_with_control_char]

# Mostrar las filas con caracteres de control
print(df_control_char_rows)

# Guardar estas filas en un archivo CSV
df_control_char_rows.to_csv('./data/control_char_rows.csv', index=False)


           Date      Time                                   Operator  \
58   1921-05-17      None                     US Aerial Mail Service   
108  1926-03-08      None                          Deutche Lufthansa   
123  1927-04-15      None                           Varney Air Lines   
128  1927-08-22  08:30:00                   KLM Royal Dutch Airlines   
129  1927-09-03      None                     Colonial Air Transport   
...         ...       ...                                        ...   
4805 2011-05-18  20:53:00                          SOL Lineas Aereas   
4819 2011-09-07  15:50:00                                YAK Service   
4864 2013-04-29  15:25:00                         National Air Cargo   
4927 2016-03-09  09:05:00                         True Aviation Ltd.   
4947 2017-02-21  09:00:00  Australian Corporate Jet Centres PTY. LTD   

     Flight_Number                         Route  \
58             NaN                           NaN   
108            NaN             

In [45]:
df_accidentes.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5008 entries, 0 to 5007
Data columns (total 19 columns):
 #   Column                              Non-Null Count  Dtype         
---  ------                              --------------  -----         
 0   Date                                5008 non-null   datetime64[ns]
 1   Time                                3287 non-null   object        
 2   Operator                            4998 non-null   object        
 3   Flight_Number                       1326 non-null   object        
 4   Route                               4245 non-null   object        
 5   Location_or_Route                   5003 non-null   object        
 6   Aircraft_Type                       4995 non-null   object        
 7   Aircraft_Registration               4736 non-null   object        
 8   Construction_Number_or_Line_Number  4341 non-null   object        
 9   Total_Aboard                        4991 non-null   Int64         
 10  Passengers_Aboard       

In [46]:
def find_control_char(row):
    """Busca caracteres de control en cada columna de una fila"""
    found_chars = []
    for col, value in row.items():
        if isinstance(value, str) and col != 'Control_Char_and_Column':
            # Buscar caracteres de control y escaparlos con repr
            if '\r' in value or '\n' in value or '\t' in value:
                escaped_value = repr(value)
                found_chars.append(f'{col}: {escaped_value}')
    return ', '.join(found_chars) if found_chars else None

# Crear una copia del DataFrame para evitar el aviso SettingWithCopyWarning
df_control_char_rows_copy = df_control_char_rows.copy()

# Aplicar la función a cada fila del DataFrame y asignar los resultados a una nueva columna
df_control_char_rows_copy['Control_Char_and_Column'] = df_control_char_rows_copy.apply(find_control_char, axis=1)


In [47]:
df_control_char_rows_copy[['Control_Char_and_Column']]

Control_Char_and_Column
58    Aircraft_Type: 'De Havilland DH-4\rDe Havillan...
108               Aircraft_Registration: 'D-290\rD-290'
123                   Aircraft_Type: 'Swallow\rSwallow'
128             Aircraft_Registration: 'H-NADU\rH-NADU'
129             Aircraft_Registration: 'NC52  \t\rNC52'
...                                                 ...
4805  Accident_Summary: 'The domestic scheduled pass...
4819  Accident_Summary: 'The plane failed to climb a...
4864  Accident_Summary: "The civilian cargo plane cr...
4927  Accident_Summary: "The cargo plane, carrying s...
4947  Accident_Summary: "The charter flight was just...

[79 rows x 1 columns]

In [48]:
unique_values = df_accidentes['Location_or_Route'].unique()
special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
print(special_values)

unique_values = df_accidentes['Aircraft_Registration'].unique()
special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
print(special_values)

unique_values = df_accidentes['Aircraft_Type'].unique()
special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
print(special_values)

unique_values = df_accidentes['Operator'].unique()
special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
print(special_values)

unique_values = df_accidentes['Route'].unique()
special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
print(special_values)

['Florianopolis, Brazil\rFlorianopolis, Brazil\rFlorianopolis, Brazil', 'Jeddah, Saudia Arabia\rJeddah, Saudia Arabia', 'Tenerife, Canary Islands, Spain\rCanary Islands', 'Moron AFB, Spain\r\t\rMoron AFB, Spain\r\t\rMoron AFB, Spain', 'Shanghai, China\r, China', 'Centeral Afghanistan\rAfghanistan', 'Djibouti City, Djibouti\r\tDjibouti City, Djibouti\rDjibouti City, Djibouti', 'Bakou, Azerbaijan\r\t\rBakou, Azerbaijan', 'Off Sarmi, Indonesia\r\t\rSarmi, Indonesia']
['D-290\rD-290', 'H-NADU\rH-NADU', 'NC52  \t\rNC52', 'NC62  \t\rNC1062', 'NC282\rNC282', 'F-AEEJ\rF-AEEJ', 'F-AIMU\rF-AIMU', 'F-AJDP\rF-AJDP', 'F-ANBL\rF-ANBL', 'P-2032\rP-2032']
['De Havilland DH-4\rDe Havilland DH-4', 'Swallow\rSwallow']
['Avio Linee Italiane\rAvio Linee Italiane', 'SAVG (S.A. Viacao Gaucha, )\rSAVG', 'Bahia Taxi Aéreo\r\t\rBahia Taxi Aéreo\r\t\rBahia Taxi Aéreo']
['Arkhangelsk - \tCherepovets', 'Havana, Cuba - \tNueva Gerona', 'Kazan - \tSverdlovsk', 'Moscow - :\tKrasnoyarsk', 'Kutaisi - \tSukhumi', 'Baku,

In [49]:
# unique_values = df_accidentes['Accident_Summary'].unique()
# special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
# print(special_values)

Como solo 79 filas tienen este problema decidí revisarlas manualmente y luego reintegrar las columnas corregidas al csv dataframe df_accidentes original.

In [50]:
df_control_char_rows_copy.to_csv('./data/control_char_rows_copy.csv', index=True)


In [51]:
# Mostrar el tipo de dato de cada elemento
df_types = df_accidentes.applymap(type)

# Ver los tipos únicos por columna
unique_types = df_types.apply(lambda x: x.unique())

# Mostrar los tipos únicos por columna
display(unique_types)

Date                                  [<class 'pandas._libs.tslibs.timestamps.Timest...
Time                                      [<class 'datetime.time'>, <class 'NoneType'>]
Operator                                               [<class 'str'>, <class 'float'>]
Flight_Number                                          [<class 'float'>, <class 'str'>]
Route                                                  [<class 'str'>, <class 'float'>]
Location_or_Route                                      [<class 'str'>, <class 'float'>]
Aircraft_Type                                          [<class 'str'>, <class 'float'>]
Aircraft_Registration                                  [<class 'float'>, <class 'str'>]
Construction_Number_or_Line_Number                     [<class 'str'>, <class 'float'>]
Total_Aboard                          [<class 'int'>, <class 'pandas._libs.missing.N...
Passengers_Aboard                     [<class 'int'>, <class 'pandas._libs.missing.N...
Crew_Aboard                     

In [55]:
df_editado = pd.read_csv('./data/control_char_rows_editado.csv')
df_editado.set_index('Unnamed: 0', inplace=True)


In [56]:
# Guardar los dtypes originales
original_dtypes = df_accidentes.dtypes

# Cambiar el dtype de todas las columnas a object
df_accidentes = df_accidentes.astype(object)

# Actualizar df_accidentes con df_editado
df_accidentes.update(df_editado)

# Cambiar el dtype de las columnas de vuelta a su dtype original
df_accidentes = df_accidentes.astype(original_dtypes)

In [57]:
# Mostrar el tipo de dato de cada elemento
df_types = df_accidentes.applymap(type)

unique_types = df_types.apply(lambda x: x.unique())

# Mostrar los tipos únicos por columna
display(unique_types)

Date                                  [<class 'pandas._libs.tslibs.timestamps.Timest...
Time                                  [<class 'datetime.time'>, <class 'NoneType'>, ...
Operator                                               [<class 'str'>, <class 'float'>]
Flight_Number                                          [<class 'float'>, <class 'str'>]
Route                                                  [<class 'str'>, <class 'float'>]
Location_or_Route                                      [<class 'str'>, <class 'float'>]
Aircraft_Type                                          [<class 'str'>, <class 'float'>]
Aircraft_Registration                                  [<class 'float'>, <class 'str'>]
Construction_Number_or_Line_Number                     [<class 'str'>, <class 'float'>]
Total_Aboard                          [<class 'int'>, <class 'pandas._libs.missing.N...
Passengers_Aboard                     [<class 'int'>, <class 'pandas._libs.missing.N...
Crew_Aboard                     

In [58]:
unique_values = df_accidentes['Location_or_Route'].unique()
special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
print(special_values)

unique_values = df_accidentes['Aircraft_Registration'].unique()
special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
print(special_values)

unique_values = df_accidentes['Aircraft_Type'].unique()
special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
print(special_values)

unique_values = df_accidentes['Operator'].unique()
special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
print(special_values)

unique_values = df_accidentes['Route'].unique()
special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
print(special_values)

unique_values = df_accidentes['Accident_Summary'].unique()
special_values = [value for value in unique_values if '\r' in str(value) or '\n' in str(value) or '\t' in str(value)]
print(special_values)

[]
[]
[]
[]
[]
[]


In [59]:
df_accidentes.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5008 entries, 0 to 5007
Data columns (total 19 columns):
 #   Column                              Non-Null Count  Dtype         
---  ------                              --------------  -----         
 0   Date                                5008 non-null   datetime64[ns]
 1   Time                                3287 non-null   object        
 2   Operator                            4998 non-null   object        
 3   Flight_Number                       1326 non-null   object        
 4   Route                               4245 non-null   object        
 5   Location_or_Route                   5003 non-null   object        
 6   Aircraft_Type                       4995 non-null   object        
 7   Aircraft_Registration               4736 non-null   object        
 8   Construction_Number_or_Line_Number  4341 non-null   object        
 9   Total_Aboard                        4991 non-null   Int64         
 10  Passengers_Aboard       

In [60]:
df_accidentes[['Date','Time']]

Date      Time
0    1908-09-17  17:18:00
1    1909-09-07      None
2    1912-07-12  06:30:00
3    1913-08-06      None
4    1913-09-09  18:30:00
...         ...       ...
5003 2021-03-28  18:35:00
5004 2021-05-21  18:00:00
5005 2021-06-10  08:00:00
5006 2021-07-04      None
5007 2021-07-06  15:00:00

[5008 rows x 2 columns]

In [72]:
# Convetir la columna 'Time' a una cadena, reemplaza los valores NaN por '00:00:00'
df_accidentes['Time'] = df_accidentes['Time'].fillna('00:00:00').astype(str)

# Unir las columnas 'Date' y 'Time' en una nueva columna 'Datetime'
df_accidentes['Datetime'] = pd.to_datetime(df_accidentes['Date'].astype(str) + ' ' + df_accidentes['Time'])

print(df_accidentes[['Datetime']].head())

# TODO Hay un vuelo con 00:00:00 valido, documentarlo en el readme: 738,"August 30, 1944",0000,"Sao Paulo, Brazil",Panair do Brasil,?,Rio de Janeiro - Sao Paulo,Lockheed 18 Lodestar,PP-PBI,2114,18,14,4,18,14,4,0,"Crashed in fog, short of the runway, while attempting to land at Congonhas Airport."
# TODO ver si dejar en texto plano la fecha y hora


             Datetime
0 1908-09-17 17:18:00
1 1909-09-07 00:00:00
2 1912-07-12 06:30:00
3 1913-08-06 00:00:00
4 1913-09-09 18:30:00


In [62]:
d = dtale.show(df_accidentes)
d.open_browser()

profile = ydata.ProfileReport(df_accidentes)
profile.to_file("report.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [63]:
profile

In [64]:
df_accidentes.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5008 entries, 0 to 5007
Data columns (total 20 columns):
 #   Column                              Non-Null Count  Dtype         
---  ------                              --------------  -----         
 0   Date                                5008 non-null   datetime64[ns]
 1   Time                                5008 non-null   object        
 2   Operator                            4998 non-null   object        
 3   Flight_Number                       1326 non-null   object        
 4   Route                               4245 non-null   object        
 5   Location_or_Route                   5003 non-null   object        
 6   Aircraft_Type                       4995 non-null   object        
 7   Aircraft_Registration               4736 non-null   object        
 8   Construction_Number_or_Line_Number  4341 non-null   object        
 9   Total_Aboard                        4991 non-null   Int64         
 10  Passengers_Aboard       

In [65]:
df_accidentes.to_parquet('./data/accidentes.parquet')

In [66]:
# Crear una nueva columna 'Decade' a partir de la columna 'Year'.
df_accidentes['Decade'] = (df_accidentes['Year'] // 10) * 10

# Agrupar los datos por década y calculando la suma total de fatalidades de la tripulación,
# la suma total de la tripulación, y el conteo total de accidentes por década.
fatality_rate_by_decade = df_accidentes.groupby('Decade').agg(
    Total_Crew_Fatalities=pd.NamedAgg(column='Crew_Fatalities', aggfunc='sum'),
    Total_Crew=pd.NamedAgg(column='Crew_Aboard', aggfunc='sum'),
    Total_Accidents=pd.NamedAgg(column='Accident_Summary', aggfunc='count')
).reset_index()

# Calcular la tasa de fatalidad por tripulante por década.
fatality_rate_by_decade['Crew_Fatality_Rate_Per_Member'] = fatality_rate_by_decade['Total_Crew_Fatalities'] / fatality_rate_by_decade['Total_Crew']

# Calcular la tasa de fatalidad de la tripulación por accidente por década.
fatality_rate_by_decade['Crew_Fatality_Rate'] = fatality_rate_by_decade['Total_Crew_Fatalities'] / fatality_rate_by_decade['Total_Accidents']

# Calcular el cambio porcentual en la tasa de fatalidad de la tripulación por accidente entre décadas.
fatality_rate_by_decade['Crew_Fatality_Rate_Change'] = fatality_rate_by_decade['Crew_Fatality_Rate'].pct_change() * 100

# Calcular la tripulación promedio por vuelo por década.
fatality_rate_by_decade['Average_Crew_Per_Flight'] = fatality_rate_by_decade['Total_Crew'] / fatality_rate_by_decade['Total_Accidents']

# Asegurar que las columnas 'Decade' sean del tipo de datos correcto.
df_accidentes['Decade'] = df_accidentes['Decade'].astype('int64')
fatality_rate_by_decade['Decade'] = fatality_rate_by_decade['Decade'].astype('int64')

# Fusionar los datos de la tasa de fatalidad de la tripulación por accidente de vuelta al DataFrame original.
df_accidentes = df_accidentes.merge(fatality_rate_by_decade[['Decade', 'Crew_Fatality_Rate']], on='Decade', how='left')

# Crear una columna de Valor Objetivo basada en un 10% de disminución en la tasa de fatalidad de la tripulación por accidente de la década anterior.
fatality_rate_by_decade[''] = fatality_rate_by_decade['Crew_Fatality_Rate'].shift(1) * 0.90

# Guardar la información en un archivo parquet
fatality_rate_by_decade.to_parquet('./data/fatality_rate_by_decade.parquet')

fatality_rate_by_decade





Decade  Total_Crew_Fatalities  Total_Crew  Total_Accidents  \
0     1900                      0           2                2   
1     1910                     52          76               30   
2     1920                    297         369              179   
3     1930                    758        1038              349   
4     1940                   1914        2264              565   
5     1950                   2481        2980              643   
6     1960                   2626        3203              642   
7     1970                   2436        3085              605   
8     1980                   1890        2611              547   
9     1990                   2127        2817              627   
10    2000                   1634        2094              507   
11    2010                    846        1025              238   
12    2020                     61          80               15   

    Crew_Fatality_Rate_Per_Member  Crew_Fatality_Rate  \
0                             0.0                 0.0   
1                        0.684211            1.733333   
2                        0.804878            1.659218   
3                         0.73025             2.17192   
4                        0.845406            3.387611   
5                         0.83255            3.858476   
6                        0.819856            4.090343   
7                        0.789627            4.026446   
8                        0.723861             3.45521   
9                        0.755059            3.392344   
10                       0.780325             3.22288   
11                       0.825366            3.554622   
12                         0.7625            4.066667   

    Crew_Fatality_Rate_Change  Average_Crew_Per_Flight            
0                        <NA>                      1.0      <NA>  
1                         inf                 2.533333       0.0  
2                   -4.275892                 2.061453      1.56  
3                   30.900215                 2.974212  1.493296  
4                   55.973101                  4.00708  1.954728  
5                   13.899628                 4.634526   3.04885  
6                    6.009284                 4.989097  3.472628  
7                   -1.562128                 5.099174  3.681308  
8                  -14.187102                 4.773309  3.623802  
9                   -1.819448                 4.492823  3.109689  
10                  -4.995507                 4.130178   3.05311  
11                  10.293346                 4.306723  2.900592  
12                  14.405043                 5.333333   3.19916

In [67]:
df_accidentes_2000 = df_accidentes[df_accidentes['Year'] >= 2000]
df_accidentes_2000[['Location_or_Route']].to_csv('ejemplo.csv', index=False)

In [68]:
import pandas as pd

us_states = {
    'Alabama', 'Alaska', 'Arizona', 'Arkansas', 'California', 'Colorado',
    'Connecticut', 'Delaware', 'Florida', 'Georgia', 'Hawaii', 'Idaho',
    'Illinois', 'Indiana', 'Iowa', 'Kansas', 'Kentucky', 'Louisiana',
    'Maine', 'Maryland', 'Massachusetts', 'Michigan', 'Minnesota',
    'Mississippi', 'Missouri', 'Montana', 'Nebraska', 'Nevada',
    'New Hampshire', 'New Jersey', 'New Mexico', 'New York',
    'North Carolina', 'North Dakota', 'Ohio', 'Oklahoma', 'Oregon',
    'Pennsylvania', 'Rhode Island', 'South Carolina', 'South Dakota',
    'Tennessee', 'Texas', 'Utah', 'Vermont', 'Virginia', 'Washington',
    'West Virginia', 'Wisconsin', 'Wyoming',
    'AL', 'AK', 'AZ', 'AR', 'CA', 'CO', 'CT', 'DE', 'FL', 'GA', 
    'HI', 'ID', 'IL', 'IN', 'IA', 'KS', 'KY', 'LA', 'ME', 'MD', 
    'MA', 'MI', 'MN', 'MS', 'MO', 'MT', 'NE', 'NV', 'NH', 'NJ', 
    'NM', 'NY', 'NC', 'ND', 'OH', 'OK', 'OR', 'PA', 'RI', 'SC', 
    'SD', 'TN', 'TX', 'UT', 'VT', 'VA', 'WA', 'WV', 'WI', 'WY'
}

regions_dict = {
    # Provincias y otras regiones
    "Ontario": "Canada",
    "Saskatchewan": "Canada",
    "Newfoundland": "Canada",
    "South Australia": "Australia",
    "Guizhou Province": "China",
    "BO": "Bolivia",  # Asumiendo que BO es una abreviatura de Bolivia
    "Scotland": "United Kingdom",
    "England": "United Kingdom",
    "Chechnya": "Russia",
    "Puerto Rico": "United States",
    # ... (agrega más si es necesario)

    # Correcciones
    "Calilfornia": "California",
    "Democtratic Republic Congo": "Democratic Republic of Congo",
    "Democratic Republic Cogo": "Democratic Republic of Congo",
    "Afghanstan": "Afghanistan",
    "Wisconson": "Wisconsin",
    "Napal": "Nepal",
    "Alaksa": "Alaska",
    "Nambia": "Namibia",
    "Mississipi": "Mississippi",
    "Democratic Republic of Congo": "Democratic Republic of Congo",
    "Democtratic Republic Congo": "Democratic Republic of Congo",
    "Democratic Republic Cogo": "Democratic Republic of Congo",
    "Congo Democratic Republic": "Democratic Republic of Congo",
    "DR Congo": "Democratic Republic of Congo",
    " Pakistan": "Pakistan",
    "South Korean": "South Korea",
    "India.": "India",
    
    # Casos especiales
    'Pepa ,Congo': 'Congo',
    'Sao Gabriel de Cachoeria': 'Brazil',
    'Near Karkov': 'Ukraine',
    'Off São Tomé Island': 'São Tomé and Príncipe',
    'Afghanistan': 'Afghanistan',
    'Off Turks and Caicos Islands': 'Turks and Caicos Islands',
    'Near Houma Louisiana': 'United States',
    'Fox Glacier Airstrip': 'New Zealand',
    'Antigua': 'Antigua and Barbuda',
    'Glasgow Scotland': 'United Kingdom',
    'Near Petreasa Romania': 'Romania',
    'South Indian Ocean': 'International Waters',
    'Java Sea': 'International Waters',
    '175 miles off the Egyptian coast': 'Egypt',
    'Malta International Airport': 'Malta'
}


# Función de normalización
def normalize_country_name(name):
    # Verificar si el nombre está en el diccionario de estados de EE.UU.
    if name in us_states:
        return "United States"
    # Acceder al diccionario para obtener el país normalizado
    return regions_dict.get(name, name)

# Definir la función para obtener el país
def get_country(location):
    parts = location.split(", ")
    if len(parts) < 2:
        return None  # indica que no se pudo identificar
    place = parts[-1]
    return normalize_country_name(place)

# Preprocesamiento
df_copy = df_accidentes_2000.copy()
df_copy['Location_Cleaned'] = df_copy['Location_or_Route'].str.replace(r'^(Near|Off) ', '')

# Identificación de casos sencillos
df_copy.loc[:, 'Country'] = df_copy['Location_Cleaned'].apply(get_country)

# Filtrado
unidentified_rows = df_copy[df_copy['Country'].isnull()]
identified_rows = df_copy.dropna(subset=['Country'])    

# Reasignar la copia modificada de nuevo al DataFrame original
df_accidentes_2000 = df_copy

# Mostrar los primeros registros para verificar
print(df_accidentes_2000[['Location_or_Route', 'Country']].head())

# Guardar el DataFrame modificado
df_accidentes_2000.to_parquet('./data/accidentes_2000_2021.parquet')



              Location_or_Route      Country
4248             Abuja, Nigeria      Nigeria
4249   Niederhasli, Switzerland  Switzerland
4250  Off Marsa el-Brega, Libya        Libya
4251       San Jose, Costa Rica   Costa Rica
4252   Off Abidjan, Ivory Coast  Ivory Coast


In [69]:
# Obtener los valores únicos de la columna 'Country'
unique_countries = df_accidentes_2000['Country'].unique()

# Guarda los valores únicos en un archivo .txt
np.savetxt('unique_countries.txt', unique_countries, fmt='%s')

In [70]:
unidentified_rows[['Location_or_Route']]

Location_or_Route
4266                       Pepa ,Congo
4470          Sao Gabriel de Cachoeria
4577                       Near Karkov
4590               Off São Tomé Island
4597                       Afghanistan
4707      Off Turks and Caicos Islands
4710              Near Houma Louisiana
4783              Fox Glacier Airstrip
4849                           Antigua
4878                  Glasgow Scotland
4882             Near Petreasa Romania
4886                South Indian Ocean
4904                          Java Sea
4934  175 miles off the Egyptian coast
4939       Malta International Airport

In [71]:
# Crear un diccionario manual para los casos no identificados
manual_country_mapping = {
    'Pepa ,Congo': 'Democratic Republic of Congo',
    'Sao Gabriel de Cachoeria': 'Brazil',
    'Near Karkov': 'Ukraine',
    'Off São Tomé Island': 'São Tomé and Príncipe',
    'Afghanistan': 'Afghanistan',
    'Off Turks and Caicos Islands': 'Turks and Caicos Islands',
    'Near Houma Louisiana': 'United States',
    'Fox Glacier Airstrip': 'New Zealand',
    'Antigua': 'Antigua and Barbuda',
    'Glasgow Scotland': 'United Kingdom',
    'Near Petreasa Romania': 'Romania',
    'South Indian Ocean': 'International Waters',
    'Java Sea': 'International Waters',
    '175 miles off the Egyptian coast': 'Egypt',
    'Malta International Airport': 'Malta'
}

# Aplicar la corrección manual
for loc, country in manual_country_mapping.items():
    df_accidentes_2000.loc[df_accidentes_2000['Location_or_Route'] == loc, 'Country'] = country

# Guardar el DataFrame modificado
df_accidentes_2000.to_parquet('./data/accidentes_2000_2021.parquet')

# Verificar si quedan filas no identificadas
unidentified_rows = df_accidentes_2000[df_accidentes_2000['Country'].isnull()]
print(unidentified_rows[['Location_or_Route']])


Empty DataFrame
Columns: [Location_or_Route]
Index: []
